# Problem Sheet 1

_Quantum Software | Oxford Computer Science 2022_


In this problem sheet, we will get the hang of working with the basic generators of circuits and ZX-diagrams concretely, using matrix calculations. For this, we will use the `sympy` library.

In [1]:
from sympy import *
from sympy.physics.quantum import TensorProduct
from fractions import Fraction

def T(*args):
    if len(args) == 1: return args[0]
    elif len(args) == 0: return Matrix([[1]])
    else: return TensorProduct(args[0], T(*args[1:]))

alpha = var("alpha")
beta = var("beta")
gamma = var("gamma")

With this library, we can construct matrices with `Matrix`. Then `*` is matrix multiplication, and `T` is tensor product.

Note `T` takes any number of arguments, e.g. $A \otimes B \otimes C$ is `T(A,B,C)`, and if you want to be fancy: $A^{\otimes n}$ is `T(*n*[A])`. (Python trivia: Why does that work??)

In [2]:
M = Matrix([[1,  2],
            [3,  4]])
display(M)
display(M * M * M)
display(T(M,M))

Matrix([
[1, 2],
[3, 4]])

Matrix([
[37,  54],
[81, 118]])

Matrix([
[1,  2,  2,  4],
[3,  4,  6,  8],
[3,  6,  4,  8],
[9, 12, 12, 16]])

We can also define some variables with `var` which can be used in mathmatical expressions, and substituted via `.subs(...)`. Variable names can be any string, but `sympy` knows how to pretty-print some variable names, e.g. Greek letters.

NOTE: $\sqrt{2}$ is `sqrt(2)`, $i$ is `I`, $\pi$ is `pi`, and $e^x$ is `exp(x)`, so phases $e^{i \alpha}$ are written `exp(i * alpha)`.

In [3]:
alpha = var("alpha")
phase = exp(I * alpha)
epi4 = exp(I * pi / 4)

display(alpha)
display(phase)
display(phase.subs(alpha, -pi / 2))
display(phase.subs(alpha, pi / 4) == epi4)
display(re(epi4) + I * im(epi4))

alpha

exp(I*alpha)

-I

True

sqrt(2)/2 + sqrt(2)*I/2

That should be enough to get going. If in doubt, [read the docs](https://docs.sympy.org/latest/index.html).

# Question 0

First some basics. Define matrices for:
 * `z0` := $|0\rangle$, `z1` := $|1\rangle$, `x0` := $|{+}\rangle$, `x1` := $|{-}\rangle$
 * `bz0` := $\langle 0|$, `bz1` := $\langle 1|$, `bx0` := $\langle {+}|$, `bx1` := $\langle {-}|$
 * `w` for the 2D identity matrix ("wire")
 * `swap` for the swap

Compute various products and tensor products and show the results are sensible.

In [4]:
#SOLUTION

z0 = Matrix([[1],[0]])
z1 = Matrix([[0],[1]])
x0 = (1/sqrt(2)) * Matrix([[1], [1]])
x1 = (1/sqrt(2)) * Matrix([[1], [-1]])

bz0, bz1, bx0, bx1 = (m.adjoint() for m in (z0,z1,x0,x1))
w = eye(2)
swap = Matrix([[1, 0, 0, 0],
               [0, 0, 1, 0],
               [0, 1, 0, 0],
               [0, 0, 0, 1]])

display(T(bz0,bz0) + T(bz1,bz1))
display(bz0 * z0)
display(bz0 * z1)
display(swap * swap == T(w,w))
display(T(swap, w) * T(w, swap) * T(swap, w) == T(w, swap) * T(swap, w) * T(w, swap))

Matrix([[1, 0, 0, 1]])

Matrix([[1]])

Matrix([[0]])

True

True

# Question 1

Define a function that produces the matrix of a Z-spider. It should take 3 arguments: `m` for input legs, `n` for output legs, and `phase` for phase. The phase should have a default value of 0.

Build this function in (at least) 2 different ways:
 1. by building the $2^n \times 2^m$ matrix of the spider explicitly (call this function `zs`)
 2. by using sums, compositions, and tensor products of the generators from the previous question

Test you implementation by comparing the matrices for various choices of inputs, outputs, and phases. (Don't forget to check no-legged spiders!)

In [5]:
# SOLUTION

def zs(m, n, phase=0):
    return Matrix([[
        (1 if i == 0 and j == 0 else 0) +
        (exp(I * phase) if i == 2**m - 1 and j == 2**n - 1 else 0)
      for i in range(2**m)] for j in range(2**n)])

def zs_gens(m, n, phase=0):
    return (
        T(*n*[z0]) * T(*m*[bz0]) +
        exp(I * phase) * T(*n*[z1]) * T(*m*[bz1])
    )

display([[zs_gens(i, j, alpha) == zs(i, j, alpha) for i in range(4)] for j in range(4)])

[[True, True, True, True],
 [True, True, True, True],
 [True, True, True, True],
 [True, True, True, True]]

# Question 2

Similarly, define a function for X-spiders:

1. by first defining the Hadamard gate `had` and using `zs` (call this function `xs`)
2. using the generators from Question 0

Again, check these two definitions agree for various numbers of legs and angles.

In [6]:
# SOLUTION

had = (1 / sqrt(2)) * Matrix([[1, 1], [1, -1]])

def xs(m, n, phase=0):
    return T(*n*[had]) * zs(m, n, phase) * T(*m*[had])

def xs_gens(m, n, phase=0):
    return (
        T(*n*[x0]) * T(*m*[bx0]) +
        exp(I * phase) * T(*n*[x1]) * T(*m*[bx1])
    )

display([[xs_gens(i, j, alpha) == xs(i, j, alpha) for i in range(4)] for j in range(4)])

[[True, True, True, True],
 [True, True, True, True],
 [True, True, True, True],
 [True, True, True, True]]

# Question 3

Verify the following equations by matrix calculation:

1. spider fusion for two Z-spiders, each having 2 inputs and 2 outputs, connected by a single leg
2. the strong complementarity rule with 2 inputs and 2 outputs
3. the Euler decomposition of the Hadamard

In each case, find the right scalar factor so the matrices of the LHS and RHS agree exactly.

**Hint:** If you have some variables, you may need to call the `simplify(...)` function before comparing matrices. If a constant phase is stuck and won't simplify any more, try splitting the real and imaginary parts and putting back together, i.e. `expr1 = re(expr) + I * im(expr)`.

In [7]:
# SOLUTION

sf_lhs = T(zs(2, 2, beta), w) * T(w, zs(2, 2, alpha))
sf_rhs = zs(3, 3, alpha + beta)
display(simplify(sf_lhs) == sf_rhs)

sc_lhs = zs(1,2) * xs(2, 1)
sc_rhs = T(xs(2, 1), xs(2, 1)) * T(w, swap, w) * T(zs(1,2), zs(1,2))
display(sc_lhs == sqrt(2) * sc_rhs)

euler_rhs = exp(-I * pi/4) * zs(1,1,pi/2) * xs(1,1,pi/2) * zs(1,1,pi/2)
display(had == re(euler_rhs) + I * im(euler_rhs))

True

True

True

# Question 4

* Make an XOR using an X spider and a scalar multiplication, and show it acts like XOR on $\{|0\rangle, |1\rangle\}$.
* Make a CNOT and TONC (a CNOT with a control on the second qubit and target on the first) using Z spiders, X spiders, swaps, and scalar multiplication. Check that CNOT acts as expected on basis states and `swap * CNOT * swap` is the same as `TONC`
* Check XOR is associative and `CNOT * TONC * CNOT = swap`

In [8]:
# SOLUTION

xor = sqrt(2) * xs(2, 1)
cnot = T(w, xor) * T(zs(1,2), w)
tonc = T(xor, w) * T(w, zs(1,2))

display(tonc == swap * cnot * swap)
display([
    xor * T(z0, z0) == z0,
    xor * T(z0, z1) == z1,
    xor * T(z1, z0) == z1,
    xor * T(z1, z1) == z0,
])
display([
    cnot * T(z0, z0) == T(z0, z0),
    cnot * T(z0, z1) == T(z0, z1),
    cnot * T(z1, z0) == T(z1, z1),
    cnot * T(z1, z1) == T(z1, z0),
])
display(xor * T(w, xor) == xor * T(xor, w))
display(cnot * tonc * cnot == swap)

True

[True, True, True, True]

[True, True, True, True]

True

True

# Question 5

Build a 2-qubit parity-phase gate, i.e. a gate that acts as: $|x, y\rangle \mapsto e^{i (x \oplus y) \alpha} |x, y\rangle$ in (at least) two ways:

1. using CNOT gates and a Z phase gate
2. using some Z-spiders and XOR

Check the two definitions coincide and act correctly on Z basis states.

In [9]:
# SOLUTION

pp1 = cnot * T(w, zs(1,1,alpha)) * cnot
pp2 = T(w, zs(1, 0, alpha) * xor, w) * T(zs(1, 2), zs(1,2))

display([
    pp1 * T(z0, z0) == T(z0, z0),
    pp1 * T(z0, z1) == exp(I * alpha) * T(z0, z1),
    pp1 * T(z1, z0) == exp(I * alpha) * T(z1, z0),
    pp1 * T(z1, z1) == T(z1, z1),
])

display(pp1 == pp2)

[True, True, True, True]

True

# Question 6

Define a function that constructs an N-qubit parity phase gate $|x_1 ... x_n\rangle \mapsto e^{i (x_1 \oplus ... \oplus x_n) \alpha} |x_1 ... x_n\rangle$ either concretely or from gates and spiders. Do this however you like, and preferably in multiple ways. Check your answers, and try to come up with cool answers. :)

In [10]:
# SOLUTION

def bits(k, n):
    return [int(b) for b in bin(k)[2:].zfill(n)]

def ppn(n, phase):
    return diag(*[exp(I * phase) if sum(bits(i, n))%2 == 1 else 1 for i in range(2**n)])

def ppn_rec(n, phase):
    if n == 1:
        return zs(1,1,phase)
    else:
        return T(cnot, eye(2**(n-2))) * T(w, ppn_rec(n-1, phase)) * T(cnot, eye(2**(n-2)))
    
ppn_rec(4, alpha) == ppn(4, alpha)

True